In [0]:
# Title: Synthetic HR Data Generator - Single Notebook (Spark DataFrame driven, no RDDs)
# Description: Generates dim_employees and 4 fact tables and writes them as Delta tables.
# Author: ChatGPT (for Akash)
# Date: 2025-11-25

In [0]:
# Cell 1 - Imports & Config
from pyspark.sql import SparkSession
from pyspark.sql.types import *
from pyspark.sql.functions import *
from pyspark.sql.window import Window

import uuid
import random
import datetime
from builtins import max


# Seed python random for reproducibility of Python parts
SEED = 42
random.seed(SEED)

spark = SparkSession.builder.appName("SyntheticHR_SingleNotebook").getOrCreate()

# Config
num_employees = 2000           # dim_employees (<3000)
snapshot_months = 36           # months for attrition snapshots -> 2000*36 = 72k rows
years_for_facts = list(range(2015, 2026))  # inclusive 2015..2025

regions = ["India", "US", "EU", "APAC", "LATAM"]
business_units = ["Engineering", "Sales", "HR", "Finance", "Operations", "Customer Success"]
roles_pool = [
    "Analyst", "Senior Analyst", "Lead Analyst",
    "Engineer I", "Engineer II", "Senior Engineer",
    "Manager", "Senior Manager", "Director", "VP"
]
grades = ["G4", "G5", "G6", "G7", "G8", "G9"]
attrition_reasons = ["Pay", "Manager", "Career Stagnation", "Personal", "Relocation", "Retirement"]

today = datetime.date.today()
hire_start = datetime.date(2010, 1, 1)

# helper for random UUID in Spark
@udf(returnType=StringType())
def gen_uuid():
    return str(uuid.uuid4())

# helper to pick from Python list in Spark (index)
def rand_choice_list(col_name, choices):
    # We'll map integer to item using array indexing: choices as literal array, index = floor(rand()*len)
    arr = array(*[lit(x) for x in choices])
    idx = (floor(rand(seed=SEED) * lit(len(choices))).cast("int"))
    return arr[idx]

In [0]:
# Cell 2 - Generate dim_employees using Spark DataFrame APIs
# We'll create a Spark range and populate fields with column expressions and UDFs.

emp_df = spark.range(0, num_employees).withColumnRenamed("id", "idx") \
    .withColumn("employee_id", gen_uuid()) \
    .withColumn("name", concat(lit("FN"), lpad(col("idx").cast("string"), 4, "0"), lit(" "), lit("LN"), lpad((col("idx") % 100).cast("string"), 2, "0"))) \
    .withColumn("gender", when(rand(seed=SEED) < 0.48, lit("Male")).when(rand(seed=SEED*2) < 0.5, lit("Female")).otherwise(lit("Other"))) \
    .withColumn("region", expr(f"array({','.join([repr(r) for r in regions])})[floor(rand()*{len(regions)})]")) \
    .withColumn("business_unit", expr(f"array({','.join([repr(b) for b in business_units])})[floor(rand()*{len(business_units)})]")) \
    .withColumn("current_role", expr(f"array({','.join([repr(r) for r in roles_pool])})[floor(rand()*{len(roles_pool)})]")) \
    .withColumn("current_grade", expr(f"array({','.join([repr(g) for g in grades])})[floor(rand()*{len(grades)})]")) \
    .withColumn("date_of_joining", expr(f"date_add('{hire_start.isoformat()}', cast(floor(rand()*{(today - hire_start).days}) as int))")) \
    .select("idx", "employee_id", "name", "gender", "region", "business_unit", "current_role", "current_grade", "date_of_joining")

# Assign managers: pick a set of manager employee_ids and assign randomly (no RDDs)
num_managers = max(60, num_employees // 12)
manager_ids_df = emp_df.orderBy(rand(seed=SEED)).limit(num_managers).select("employee_id").withColumnRenamed("employee_id", "manager_candidate_id")
# Add an index to manager candidates to sample from
manager_ids_df = manager_ids_df.withColumn("mgr_idx", monotonically_increasing_id())

# Cross join approach: create a random integer per employee and map to manager_candidates by modulo
emp_df = emp_df.withColumn("rand_num", (floor(rand(seed=SEED+1) * lit(1000000))).cast("long"))
# Collect manager candidates into an array using aggregation (small set; safe)
manager_list = [row.manager_candidate_id for row in manager_ids_df.collect()]
# Broadcast manager list into a column:
emp_df = emp_df.withColumn("manager_id", expr(f"array({','.join([repr(m) for m in manager_list])})[floor(rand()*{len(manager_list)})]"))

# Set some top-level null managers (3%):
emp_df = emp_df.withColumn("manager_id", when(rand(seed=SEED+2) < 0.03, lit(None)).otherwise(col("manager_id")))

# Add tenure calculations
emp_df = emp_df.withColumn("tenure_days", datediff(current_date(), col("date_of_joining"))) \
               .withColumn("tenure_years", round(col("tenure_days") / 365.0, 2))

# Persist employees DF for further joins
display(emp_df.limit(10))

idx employee_id name gender region business_unit current_role current_grade date_of_joining rand_num manager_id tenure_days tenure_years 0 10e5a8d9-ac08-49a8-8e62-5d17eafed11f FN0000 LN00 Female US Finance Senior Engineer G7 2012-01-12 801753 67452fc6-a56d-4243-9933-e6f6a844f96f 5066 13.88 1 d0cd2773-b57b-4e4a-a24f-5cdd9af822a8 FN0001 LN01 Other India Engineering Engineer I G6 2025-06-15 656555 9bef5894-55b3-456d-aaaa-b3c6c5c3196b 163 0.45 2 63e594a3-b395-40e9-b36a-c26da99059be FN0002 LN02 Female LATAM Sales Lead Analyst G8 2016-09-23 251559 13e29c65-7eec-492d-b70d-f0d5279c605b 3350 9.18 3 04b9db24-1976-4386-9a4f-f388fa32a965 FN0003 LN03 Male EU Engineering VP G5 2020-04-27 207342 24e5f379-504a-4ffa-ab29-9514b29c2ecd 2038 5.58 4 5fa7cf98-5117-4cf4-a8a0-ba36e793fec6 FN0004 LN04 Female APAC Sales Senior Manager G6 2011-01-26 639292 d111477f-a912-44a9-bb60-65fbdf2a84aa 5417 14.84 5 416e6dfc-8e83-43ff-a393-1c0fe9ec6b9f FN0005 LN05 Other India Customer Success Senior Engineer G4 2014-07-24 850558 cd6e86e9-82f7-46c1-ba9b-fe69093a787f 4142 11.35 6 0e739488-6407-403d-be16-32b5f4c6112f FN0006 LN06 Other LATAM Engineering Engineer II G6 2020-06-06 818471 107d855a-d16e-46ef-bccb-512aed2eb095 1998 5.47 7 dca762b0-6425-4c3b-8082-ad55f0c541d5 FN0007 LN07 Male US Customer Success VP G5 2021-10-06 755550 8c2de9a1-e59f-4e09-918e-9b117d577b82 1511 4.14 8 6191ce20-1459-4659-b317-702f8087414d FN0008 LN08 Other APAC Engineering Engineer II G7 2017-02-10 343804 4bdbedaf-0804-4883-a292-9f22cad08935 3210 8.79 9 462436fb-0666-4ee0-987d-28a792e28efb FN0009 LN09 Female LATAM Operations Director G4 2016-04-12 75312 18f919b1-8518-42b1-9f0f-cc302f494e18 3514 9.63

In [0]:
# Cell 3 - Generate fact_role_history
# We'll create role history by generating a varying number of role records per employee using explode on an array of counts.
# Approach: for each employee create an array of N positions (N sampled via expression), then explode.

# Function to create a DataFrame mapping each employee to a random number of roles via DataFrame expressions
# Create a helper DF with sequence array lengths per employee
emp_counts_df = emp_df.select(
    "employee_id", "date_of_joining", "business_unit", "region"
).withColumn(
    "num_roles",
    when(rand(seed=SEED+3) < 0.05, lit(3))
     .otherwise( ((abs(rand(seed=SEED+4)) * lit(10) + lit(6)).cast("int")) )
)
# clamp to 1..20
emp_counts_df = emp_counts_df.withColumn("num_roles", least(lit(20), greatest(lit(1), col("num_roles"))))

# Create an array of positions [0..num_roles-1] and explode to get one row per role
role_history_df = emp_counts_df.withColumn("pos_array", expr("sequence(1, num_roles)")) \
    .withColumn("pos", explode(col("pos_array"))) \
    .drop("pos_array")

# Now assign role, grade, start/end dates using row_number-like calculations per employee
# We'll compute role_start_date as date_of_joining + cumulative months
# To create variable durations, generate a random months_in_role per pos using rand() keyed by pos and employee_id
role_history_df = role_history_df.withColumn("months_in_role", (floor(rand(seed=SEED+10) * 31) + 6).cast("int"))  # 6..36
# We need a cumulative months offset per employee: use window sum over pos - 1
w_pos = Window.partitionBy("employee_id").orderBy("pos").rowsBetween(Window.unboundedPreceding, -1)
role_history_df = role_history_df.withColumn("cum_months_before", coalesce(sum("months_in_role").over(w_pos), lit(0)))
# start_date = date_add(date_of_joining, 30 * cum_months_before)
role_history_df = role_history_df.withColumn("role_start_date", expr("date_add(date_of_joining, cast(cum_months_before*30 as int))"))
# tentative end date = start_date + months_in_role*30; if beyond current_date, set null
role_history_df = role_history_df.withColumn("role_end_date_temp", expr("date_add(role_start_date, cast(months_in_role*30 as int))"))
role_history_df = role_history_df.withColumn("role_end_date",
    when(col("role_end_date_temp") > current_date(), lit(None)).otherwise(col("role_end_date_temp"))
).drop("role_end_date_temp", "cum_months_before", "num_roles", "pos", "months_in_role")

# Assign random role and grade values via array indexing
role_history_df = role_history_df.withColumn("role", expr(f"array({','.join([repr(r) for r in roles_pool])})[floor(rand()*{len(roles_pool)})]")) \
    .withColumn("grade", expr(f"array({','.join([repr(g) for g in grades])})[floor(rand()*{len(grades)})]")) \
    .select("employee_id", "role", "grade", "role_start_date", "role_end_date", "business_unit", "region")

# Add role_end_date_clamped and time_in_role_days
role_history_df = role_history_df.withColumn("role_end_date_clamped", coalesce(col("role_end_date"), current_date())) \
    .withColumn("time_in_role_days", datediff(col("role_end_date_clamped"), col("role_start_date")))

# Compute promotion_flag by grade rank using a window
role_history_df = role_history_df.withColumn("grade_rank",
    when(col("grade") == "G4", lit(4))
    .when(col("grade") == "G5", lit(5))
    .when(col("grade") == "G6", lit(6))
    .when(col("grade") == "G7", lit(7))
    .when(col("grade") == "G8", lit(8))
    .when(col("grade") == "G9", lit(9)).otherwise(lit(6))
)

w_r = Window.partitionBy("employee_id").orderBy("role_start_date")
role_history_df = role_history_df.withColumn("prev_grade_rank", lag("grade_rank").over(w_r)) \
    .withColumn("promotion_flag", when(col("prev_grade_rank").isNotNull() & (col("grade_rank") > col("prev_grade_rank")), lit(1)).otherwise(lit(0)))

# Ensure fact size: check count (should be >20k)
# (We will assert later after all DFs built)
display(role_history_df.limit(10))

employee_id role grade role_start_date role_end_date business_unit region role_end_date_clamped time_in_role_days grade_rank prev_grade_rank promotion_flag 0031bcee-174c-4719-8348-e5bd72e7769e Analyst G5 2016-12-26 2019-09-12 Customer Success APAC 2019-09-12 990 5 null 0 0031bcee-174c-4719-8348-e5bd72e7769e Manager G6 2019-09-12 2021-10-31 Customer Success APAC 2021-10-31 780 6 5 1 0031bcee-174c-4719-8348-e5bd72e7769e Analyst G5 2021-10-31 2023-05-24 Customer Success APAC 2023-05-24 570 5 6 0 0031bcee-174c-4719-8348-e5bd72e7769e Manager G6 2023-05-24 null Customer Success APAC 2025-11-25 916 6 5 1 0031bcee-174c-4719-8348-e5bd72e7769e Analyst G9 2025-12-09 null Customer Success APAC 2025-11-25 -14 9 6 1 0031bcee-174c-4719-8348-e5bd72e7769e Engineer II G6 2028-10-24 null Customer Success APAC 2025-11-25 -1064 6 9 0 003364fd-e809-4e8b-8011-9f53a8e31025 Senior Manager G8 2010-05-07 2011-07-01 Operations LATAM 2011-07-01 420 8 null 0 003364fd-e809-4e8b-8011-9f53a8e31025 Senior Manager G7 2011-07-01 2012-11-22 Operations LATAM 2012-11-22 510 7 8 0 003364fd-e809-4e8b-8011-9f53a8e31025 VP G7 2012-11-22 2013-07-20 Operations LATAM 2013-07-20 240 7 7 0 003364fd-e809-4e8b-8011-9f53a8e31025 Lead Analyst G9 2013-07-20 2015-05-11 Operations LATAM 2015-05-11 660 9 7 1

In [0]:
# Cell 4 - Generate fact_performance (yearly) using DataFrame cross join trick (employee * years)
from pyspark.sql.functions import create_map, lit, rand, round as spark_round

# grade bias pairs
grade_bias_pairs = [("G4", -0.2), ("G5", -0.1), ("G6", 0.0), ("G7", 0.1), ("G8", 0.2), ("G9", 0.3)]

# Build args for create_map as [lit("G4"), lit(-0.2), lit("G5"), lit(-0.1), ...]
map_args = []
for g, v in grade_bias_pairs:
    map_args.append(lit(g))
    map_args.append(lit(v))

grade_bias_expr = create_map(*map_args)
years_df = spark.createDataFrame([(y,) for y in years_for_facts], StructType([StructField("year", IntegerType())]))
perf_base = emp_df.select("employee_id", "current_grade", "manager_id").crossJoin(years_df)
# Now build performance DF (perf_base assumed to be defined)
# Use spark functions and avoid Python built-in names
perf_df = perf_base.withColumn("g_bias", grade_bias_expr.getItem(col("current_grade"))) \
    .withColumn("rating_raw", (spark_round(rand(seed=SEED+20) * 1.8 + (lit(3) + coalesce(col("g_bias"), lit(0.0))), 0)).cast("int")) \
    .withColumn("rating", when(col("rating_raw") < 1, lit(1)).when(col("rating_raw") > 5, lit(5)).otherwise(col("rating_raw")).cast("int")) \
    .withColumn("potential_flag", when((col("rating") >= 4) & (rand(seed=SEED+21) < 0.35), lit(1)).otherwise(lit(0))) \
    .withColumnRenamed("manager_id", "reviewer_id") \
    .select("employee_id", "year", "rating", "potential_flag", "reviewer_id")

# add 3-year rolling avg
from pyspark.sql.window import Window
from pyspark.sql.functions import avg
w_emp_year = Window.partitionBy("employee_id").orderBy("year").rowsBetween(-2, 0)
perf_df = perf_df.withColumn("rating_3yr_avg", round(avg("rating").over(w_emp_year), 2))


/databricks/python/lib/python3.12/site-packages/pyspark/sql/connect/column.py:512: FutureWarning: A column as 'key' in getItem is deprecated as of Spark 3.0, and will not be supported in the future release. Use `column[key]` or `column.key` syntax instead.
  warnings.warn(


In [0]:
# Cell 5 - Generate fact_compensation (yearly) using cross join and formulas
from pyspark.sql.functions import create_map, lit

# --- Compensation mappings ---
grade_base_map = {
    "G4": 400000,
    "G5": 700000,
    "G6": 1100000,
    "G7": 1700000,
    "G8": 2500000,
    "G9": 4000000
}

# Build arguments for create_map
grade_map_args = []
for g, v in grade_base_map.items():
    grade_map_args.append(lit(g))
    grade_map_args.append(lit(v))

grade_base_map_sql = create_map(*grade_map_args)

# --- Region multiplier mapping ---
region_mult_map = {
    "India": 1.0,
    "US": 3.5,
    "EU": 2.5,
    "APAC": 1.2,
    "LATAM": 1.1
}

region_map_args = []
for r, v in region_mult_map.items():
    region_map_args.append(lit(r))
    region_map_args.append(lit(v))

region_mult_map_sql = create_map(*region_map_args)


comp_base = emp_df.select("employee_id", "current_grade", "region").crossJoin(years_df)
from pyspark.sql.functions import col, lit, rand

# Compute earliest fact year safely (avoid Spark min shadowing)
import builtins
min_years_for_facts = builtins.min(years_for_facts)

comp_df = (
    comp_base
        # Use modern bracket access instead of getItem
        .withColumn("grade_base", grade_base_map_sql[col("current_grade")])
        .withColumn("region_mult", region_mult_map_sql[col("region")])

        # Base compensation with random banding
        .withColumn(
            "base",
            (
                col("grade_base") *
                col("region_mult") *
                (1 + (rand(seed=SEED+30) * 0.2 - 0.08))
            ).cast("long")
        )

        # Tenure influence
        .withColumn("years_since", col("year") - lit(min_years_for_facts))

        # Salary growth + noise
        .withColumn(
            "salary",
            (
                col("base") *
                (1 + lit(0.045) * col("years_since")) *
                (1 + (rand(seed=SEED+31) * 0.09 - 0.03))
            ).cast("long")
        )

        # Bonus (3% to ~20%)
        .withColumn(
            "bonus",
            (
                col("salary") *
                (lit(0.03) + rand(seed=SEED+32) * lit(0.17))
            ).cast("long")
        )

        # Final output columns
        .select(
            "employee_id",
            "year",
            "salary",
            "bonus",
            col("current_grade").alias("grade"),
            "region"
        )
)


# median by grade-year and compa_ratio
median_by_grade_year_df = comp_df.groupBy("grade", "year").agg(expr("percentile_approx(salary, 0.5) as median_salary"))
comp_df = comp_df.join(median_by_grade_year_df, on=["grade","year"], how="left") \
    .withColumn("compa_ratio", round(col("salary") / col("median_salary"), 3))

# salary YoY growth
w_comp = Window.partitionBy("employee_id").orderBy("year")
comp_df = comp_df.withColumn("salary_prev", lag("salary").over(w_comp)) \
    .withColumn("salary_growth_pct", round(when(col("salary_prev").isNotNull(), (col("salary") - col("salary_prev"))/col("salary_prev")*100).otherwise(lit(0.0)), 2))

In [0]:
# Cell 6 - Generate fact_attrition_snapshots (monthly snapshots) using DataFrame approach
# We'll create a months DF and cross join with employees, then compute attrition flags.
from pyspark.sql.functions import sequence, to_date

start_snapshot_date = today - datetime.timedelta(days=30*(snapshot_months - 1))
start_date_str = start_snapshot_date.isoformat()

months = [ (start_snapshot_date + datetime.timedelta(days=30*i)).isoformat() for i in range(snapshot_months) ]
months_df = spark.createDataFrame([(m,) for m in months], StructType([StructField("snapshot_date_str", StringType())])) \
    .withColumn("snapshot_date", to_date(col("snapshot_date_str"))).drop("snapshot_date_str")

# Cross join employees with months => large DF (~72k rows)
snap_df = emp_df.select("employee_id", "date_of_joining", "manager_id","tenure_days").crossJoin(months_df)

# Filter snapshots before employee joined
snap_df = snap_df.filter(col("snapshot_date") >= col("date_of_joining"))


# Simulate exits: choose ~18% of employees to have an exit month; create a temp mapping table
# We'll create a small mapping DF by sampling employees and assigning exit month
exit_prob = 0.18
sampled_exits = emp_df.withColumn("exit_flag", when(rand(seed=SEED+40) < exit_prob, lit(1)).otherwise(lit(0))) \
    .filter(col("exit_flag") == 1) \
    .select("employee_id") \
    .withColumn("random_month_idx", (floor(rand(seed=SEED+41) * lit(snapshot_months))).cast("int")) \
    .withColumn("exit_date", expr(f"date_add('{start_date_str}', cast(random_month_idx*30 as int))")) \
    .select("employee_id", "exit_date")

# Left join mapped exit_date on snapshots to determine attrition_flag for that month
snap_df = snap_df.join(sampled_exits, on="employee_id", how="left")

# Attrition flags: if exit_date is same month & year as snapshot_date then attr_flag=1
snap_df = snap_df.withColumn("attrition_flag", when((col("exit_date").isNotNull()) & (year("exit_date") == year("snapshot_date")) & (month("exit_date") == month("snapshot_date")), lit(1)).otherwise(lit(0)))

# attrition_reason: if attr_flag then choose reason biased by mobility or compa_ratio later; as placeholder random choice
snap_df = snap_df.withColumn("attrition_reason", when(col("attrition_flag") == 1, expr(f"array({','.join([repr(r) for r in attrition_reasons])})[floor(rand()*{len(attrition_reasons)})]")).otherwise(lit(None)))

import pyspark.sql.functions as F
# notice period random for attritions
snap_df = snap_df.withColumn(
    "notice_period_days",
    when(
        col("attrition_flag") == 1,
        element_at(
            F.array(F.lit(0), F.lit(15), F.lit(30), F.lit(60), F.lit(90)),
            (F.floor(F.rand(seed=SEED+42) * 5) + 1).cast("int")
        )
    ).otherwise(F.lit(None))
)

# We'll later compute mobility_count and career_stagnation_flag per employee and join; compute mobility_count from role_history_df
import pyspark.sql.functions as F

mobility_df = (
    role_history_df
        .groupBy("employee_id")
        .agg(
            F.count("*").alias("mobility_count"),
            F.max("role_end_date_clamped").alias("last_role_change_date")
        )
)

snap_df = snap_df.join(mobility_df, "employee_id", how="left").na.fill({"mobility_count": 0})

# career stagnation flag: months since last_role_change >=24
snap_df = snap_df.withColumn("months_since_last_role_change", when(col("last_role_change_date").isNotNull(), round(expr("months_between(snapshot_date, last_role_change_date)"),1)).otherwise(None)) \
    .withColumn("career_stagnation_flag", when(col("months_since_last_role_change") >= 24, lit(1)).otherwise(lit(0)))

snap_df = snap_df.withColumn(
    "months_between",
    F.months_between(F.col("snapshot_date"), F.col("exit_date"))
)

# Base risk score formula per snapshot row
snap_df = snap_df.withColumn(
    "base_risk",
    F.lit(0.05)
    + F.when(F.col("months_between").isNull(), F.lit(0)).otherwise(F.lit(0))
    + F.when(F.col("tenure_days").isNull(), F.lit(0)).otherwise(F.lit(0))
)


# We can't reference tenure_days easily after crossJoin; compute tenure_years per snapshot as months between snapshot_date and doj
snap_df = snap_df.withColumn("tenure_years_snapshot", F.round(datediff(col("snapshot_date"), F.col("date_of_joining"))/365.0, 2))
snap_df = snap_df.withColumn("predicted_attrition_risk",
                             F.round(
                                 (F.lit(0.04)
                                  + F.when(F.col("tenure_years_snapshot") < 1, 0.12).otherwise(0.0)
                                  + F.when(F.col("mobility_count") == 0, 0.08).otherwise(0.0)
                                  + F.when(F.col("career_stagnation_flag") == 1, 0.10).otherwise(0.0)
                                  + F.rand(seed=SEED+50)*0.2
                                 ), 3)
                            )

# Select final snapshot columns
attrition_snap_df = snap_df.select(
    "employee_id",
    "snapshot_date",
    "attrition_flag",
    "exit_date",
    "attrition_reason",
    "notice_period_days",
    "mobility_count",
    "career_stagnation_flag",
    F.col("predicted_attrition_risk").alias("predicted_attrition_risk"),
    "manager_id"
)

In [0]:
display(attrition_snap_df)

employee_id snapshot_date attrition_flag exit_date attrition_reason notice_period_days mobility_count career_stagnation_flag predicted_attrition_risk manager_id 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-01-10 0 null null null 0 0 0.144 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-02-09 0 null null null 0 0 0.175 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-03-11 0 null null null 0 0 0.132 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-04-10 0 null null null 0 0 0.123 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-05-10 0 null null null 0 0 0.208 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-06-09 0 null null null 0 0 0.254 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-07-09 0 null null null 0 0 0.151 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-08-08 0 null null null 0 0 0.179 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-09-07 0 null null null 0 0 0.298 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-10-07 0 null null null 0 0 0.227 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-11-06 0 null null null 0 0 0.232 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2023-12-06 0 null null null 0 0 0.303 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-01-05 0 null null null 0 0 0.182 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-02-04 0 null null null 0 0 0.276 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-03-05 0 null null null 0 0 0.25 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-04-04 0 null null null 0 0 0.309 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-05-04 0 null null null 0 0 0.253 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-06-03 0 null null null 0 0 0.23 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-07-03 0 null null null 0 0 0.263 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-08-02 0 null null null 0 0 0.163 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-09-01 0 null null null 0 0 0.283 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-10-01 0 null null null 0 0 0.263 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-10-31 0 null null null 0 0 0.218 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-11-30 0 null null null 0 0 0.131 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2024-12-30 0 null null null 0 0 0.256 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2025-01-29 0 null null null 0 0 0.299 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2025-02-28 0 null null null 0 0 0.242 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2025-03-30 0 null null null 0 0 0.292 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2025-04-29 0 null null null 0 0 0.193 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2025-05-29 0 null null null 0 0 0.268 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2025-06-28 0 null null null 0 0 0.285 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2025-07-28 0 null null null 0 0 0.222 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2025-08-27 0 null null null 0 0 0.29 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997ff 2025-09-26 0 null null null 0 0 0.201 a1bff46f-53b5-4c1b-9587-5d278f4711be 10ccf5a5-d26d-41cd-99ec-d2cb969997

In [0]:
# Cell 7 - Derived calculations on employees (join comp & perf latest)
# Latest year
latest_year = builtins.max(years_for_facts)
latest_comp_df = comp_df.filter(col("year") == latest_year).select("employee_id", "compa_ratio")
latest_perf_df = perf_df.filter(col("year") == latest_year).select("employee_id",F.col("rating").alias("latest_rating"), F.col("rating_3yr_avg").alias("latest_rating_3yr_avg"))

from pyspark.sql import functions as F

# ---------------------------- #
# 1. RENAME COLUMNS EXPLICITLY #
# ---------------------------- #

# mobility_df
mobility_df = mobility_df.withColumnRenamed("mobility_count", "mobility_count_mb")

# compensation latest snapshot
latest_comp_df = latest_comp_df.withColumnRenamed("compa_ratio", "latest_compa_ratio")

# performance latest snapshot
latest_perf_df = (
    latest_perf_df
    .withColumnRenamed("rating", "latest_rating")
    .withColumnRenamed("rating_3yr_avg", "latest_rating_3yr_avg")
)

# attrition snapshot
attrition_snap_df = (
    attrition_snap_df
    .withColumnRenamed("attrition_flag", "latest_attrition_flag")
    .withColumnRenamed("manager_id", "attrition_manager_id")
)

# ---------------------------------------- #
# 2. JOIN ALL INTO employees_enriched_df   #
# ---------------------------------------- #

employees_enriched_df = (
    emp_df
    .join(mobility_df, "employee_id", "left")
    .join(latest_comp_df, "employee_id", "left")
    .join(latest_perf_df, "employee_id", "left")
    .join(attrition_snap_df, "employee_id", "left")
)

# --------------------------- #
# 3. CLEANUP & DEFAULT VALUES #
# --------------------------- #

employees_enriched_df = (
    employees_enriched_df
    .withColumn("compa_ratio", F.coalesce(F.col("latest_compa_ratio"), F.lit(1.0)))
    .withColumn("latest_rating", F.coalesce(F.col("latest_rating"), F.lit(3)))
    .withColumn("latest_rating_3yr_avg", F.coalesce(F.col("latest_rating_3yr_avg"), F.lit(3.0)))
)

# ------------------------------------------------------------- #
# 4. FINAL — ATTRITION RISK SCORE WITH CLEAN COLUMN REFERENCE   #
# ------------------------------------------------------------- #

employees_enriched_df = employees_enriched_df.withColumn(
    "attrition_risk_score",
    F.round(
        F.lit(0.04)
        + F.when(F.col("tenure_years") < 1, 0.12).otherwise(0.0)
        + F.when(F.col("career_stagnation_flag") == 1, 0.10).otherwise(0.0)
        + F.when(F.col("mobility_count_mb") == 0, 0.08).otherwise(0.0)
        - F.when(F.col("latest_rating_3yr_avg") >= 4.0, 0.06).otherwise(0.0),
        3
    )
)

# display(employees_enriched_df)


# Add manager aggregates (manager_avg_team_rating from performance latest year)
manager_avg_rating_df = perf_df.filter(F.col("year") == latest_year).groupBy("reviewer_id").agg(F.round(F.avg("rating"),2).alias("manager_avg_team_rating"))
employees_enriched_df = employees_enriched_df.join(manager_avg_rating_df, employees_enriched_df.manager_id == manager_avg_rating_df.reviewer_id, how="left").drop("reviewer_id")
employees_enriched_df = employees_enriched_df.na.fill({"manager_avg_team_rating": 3.0})

display(employees_enriched_df.limit(10))

employee_id idx name gender region business_unit current_role current_grade date_of_joining rand_num manager_id tenure_days tenure_years mobility_count_mb last_role_change_date latest_compa_ratio latest_rating latest_rating_3yr_avg snapshot_date latest_attrition_flag exit_date attrition_reason notice_period_days mobility_count career_stagnation_flag predicted_attrition_risk attrition_manager_id compa_ratio attrition_risk_score manager_avg_team_rating 5e950c24-0ddc-43e8-9fb0-b3da21774a2f 7 FN0007 LN07 Male India HR Lead Analyst G8 2017-05-03 755550 20af0bf4-9a80-4de0-86af-807a9825c39f 3128 8.57 null null null 3 3.0 null null null null null null null null null 1.0 0.04 4.0 94156568-e58e-41e7-8fc5-aed3637c4653 2 FN0002 LN02 Female US Engineering Engineer I G6 2011-12-31 251559 1c5df975-127b-4c71-b4a7-59452c435686 5078 13.91 null null null 3 3.0 null null null null null null null null null 1.0 0.04 3.93 a777d106-0839-4bad-94f1-db26e22a0741 4 FN0004 LN04 Female APAC HR VP G8 2013-11-14 639292 38a62bed-5157-4db4-9f35-dbfff74f9c0a 4394 12.04 null null null 3 3.0 null null null null null null null null null 1.0 0.04 4.27 1b29e0b6-f46b-40f2-8848-9d4dbb270047 0 FN0000 LN00 Female India HR Senior Manager G8 2012-05-15 801753 a1bff46f-53b5-4c1b-9587-5d278f4711be 4942 13.54 null null null 3 3.0 null null null null null null null null null 1.0 0.04 3.88 3fe46504-305a-4b58-840a-9e6663e90415 5 FN0005 LN05 Other India Operations Lead Analyst G6 2012-04-26 850558 53e96546-15ba-4ab2-be3c-e381977414e5 4961 13.59 null null null 3 3.0 null null null null null null null null null 1.0 0.04 4.0 b5e7d0b3-417b-4146-b699-0e35981e9719 6 FN0006 LN06 Other EU Sales Senior Analyst G5 2012-07-21 818471 1f960f37-d52b-491b-84c1-6d0c1a51d7bf 4875 13.36 null null null 3 3.0 null null null null null null null null null 1.0 0.04 3.7 c3ad2020-4c77-4822-978e-523228a8a19a 1 FN0001 LN01 Other LATAM Operations Senior Analyst G7 2011-08-06 656555 27195713-0a32-4349-9593-2bf4c120b0f8 5225 14.32 null null null 3 3.0 null null null null null null null null null 1.0 0.04 3.78 994588aa-9b66-4ae1-b3c6-2360b44db926 8 FN0008 LN08 Other US HR Lead Analyst G4 2020-01-13 343804 a07db4a2-3689-4508-921b-8801c8bf8bc0 2143 5.87 null null null 3 3.0 null null null null null null null null null 1.0 0.04 4.33 91d70076-386a-486e-90a8-3d268b274139 3 FN0003 LN03 Male LATAM Engineering Manager G8 2010-04-14 207342 20af0bf4-9a80-4de0-86af-807a9825c39f 5704 15.63 null null null 3 3.0 null null null null null null null null null 1.0 0.04 4.0 1ac32729-584f-40c5-bd89-a01198380400 9 FN0009 LN09 Female APAC Engineering Manager G9 2014-01-06 75312 03fb64fe-d635-4c0f-8516-ea5457ca676b 4341 11.89 null null null 3 3.0 null null null null null null null null null 1.0 0.04 4.06

In [0]:
# Cell 8 - Sanity checks & assertions on counts (must satisfy constraints)
dim_count = employees_enriched_df.count()
role_history_count = role_history_df.count()
performance_count = perf_df.count()
compensation_count = comp_df.count()
attrition_count = attrition_snap_df.count()

print("Counts:")
print("dim_employees:", dim_count)
print("fact_role_history:", role_history_count)
print("fact_performance:", performance_count)
print("fact_compensation:", compensation_count)
print("fact_attrition_snapshots:", attrition_count)

# Basic assertions (raise if not satisfied)
assert dim_count < 3000, f"employees dim exceeds 3000 ({dim_count})"
assert role_history_count > 20000, f"role_history fact must be >20k ({role_history_count})"
assert performance_count > 20000, f"performance fact must be >20k ({performance_count})"
assert compensation_count > 20000, f"compensation fact must be >20k ({compensation_count})"
assert attrition_count > 20000, f"attrition snapshots fact must be >20k ({attrition_count})"

Counts:
dim_employees: 2000
fact_role_history: 20167
fact_performance: 22000
fact_compensation: 22000
fact_attrition_snapshots: 65449


In [0]:
# Cell 9 - Write as Delta tables (Databricks)
database = "akash_s_demo.talent"
spark.sql(f"CREATE DATABASE IF NOT EXISTS {database}")

employees_enriched_df.write.format("delta").mode("overwrite").saveAsTable(f"{database}.dim_employees")
role_history_df.write.format("delta").mode("overwrite").saveAsTable(f"{database}.fact_role_history")
perf_df.write.format("delta").mode("overwrite").saveAsTable(f"{database}.fact_performance")
comp_df.write.format("delta").mode("overwrite").saveAsTable(f"{database}.fact_compensation")
attrition_snap_df.write.format("delta").mode("overwrite").saveAsTable(f"{database}.fact_attrition_snapshots")

print("All tables written to Delta under database:", database)

All tables written to Delta under database: akash_s_demo.talent


In [0]:
# Cell 10 - Example SQL queries for leadership questions (copy/paste into SQL editor)
print("=== Example SQL Queries ===")
print("-- 1) Top employees by attrition risk")
print(f"SELECT employee_id, name, business_unit, current_role, current_grade, tenure_years, mobility_count, career_stagnation_flag, attrition_risk_score FROM {database}.dim_employees ORDER BY attrition_risk_score DESC LIMIT 50;")
print()
print("-- 2) Which managers have highest attrition (hotspots)?")
print(f"SELECT manager_id, manager_attrition_rate_pct, manager_attritions_count FROM {database}.dim_employees GROUP BY manager_id, manager_attrition_rate_pct, manager_attritions_count ORDER BY manager_attrition_rate_pct DESC LIMIT 50;")
print()
print("-- 3) Average time-in-role (months) by business unit")
print(f"SELECT business_unit, ROUND(AVG(time_in_role_days)/30,1) as avg_months_in_role FROM {database}.fact_role_history GROUP BY business_unit ORDER BY avg_months_in_role DESC;")
print()
print("-- 4) Do promoted employees have lower attrition? (Promoted vs Not Promoted)")
print(f\"\"\"WITH promos AS (
    SELECT employee_id, SUM(promotion_flag) as promotions
    FROM {database}.fact_role_history
    GROUP BY employee_id
), snaps AS (
    SELECT employee_id, MAX(attrition_flag) as ever_left
    FROM {database}.fact_attrition_snapshots
    GROUP BY employee_id
)
SELECT CASE WHEN promotions>0 THEN 'Promoted' ELSE 'Not Promoted' END as promo_group,
       ROUND(SUM(ever_left)/COUNT(*)*100,2) as percent_left
FROM promos p JOIN snaps s ON p.employee_id = s.employee_id
GROUP BY promo_group;\"\"\")

In [0]:
%sql
SELECT employee_id, name, business_unit, current_role, current_grade, tenure_years, mobility_count, career_stagnation_flag, attrition_risk_score FROM akash_s_demo.talent.dim_employees ORDER BY attrition_risk_score DESC LIMIT 50

employee_id name business_unit current_role current_grade tenure_years mobility_count career_stagnation_flag attrition_risk_score ed122187-99dc-47ac-bcbe-5d7fddaa0b0b FN0242 LN42 HR VP G8 0.41 null null 0.16 6a1dfcca-e89f-4cc6-807c-8caf4d52a1c7 FN1693 LN93 Engineering Manager G8 0.55 null null 0.16 d5cd7a6c-dc84-4f97-8234-cda8de87ca54 FN1144 LN44 HR Senior Manager G4 0.87 null null 0.16 83b5ea26-2448-441b-b0e5-c3fb602bde26 FN0075 LN75 Engineering Senior Analyst G9 0.4 null null 0.16 3c8c524d-c607-40b6-9051-e5442543e4b3 FN1622 LN22 HR Senior Manager G9 0.31 null null 0.16 e8252cef-d6b3-470f-b762-545863eb925f FN1656 LN56 Customer Success Analyst G8 0.28 null null 0.16 88650ec0-e8f4-436f-830a-a9e8c1827769 FN1200 LN00 Customer Success Director G4 0.3 null null 0.16 5f501993-9bf9-4d1d-8e93-1a2257be6c5a FN1196 LN96 HR Manager G9 0.78 null null 0.16 cc7093c9-a113-4c5e-840a-1719f1e816b2 FN0070 LN70 HR VP G5 0.28 null null 0.16 f9cf03fa-e065-4781-8d6c-d995cfb13033 FN0177 LN77 Sales Engineer II G5 0.42 null null 0.16 bc207020-a1c6-4068-9a82-1c87199e1814 FN1514 LN14 Customer Success Analyst G7 0.03 null null 0.16 cc69626e-b2ab-449f-a2a7-e096487c39c1 FN0176 LN76 Operations VP G7 0.83 null null 0.16 f936cd2c-e247-4e67-8b8e-6bd09da279ae FN0241 LN41 Engineering Engineer II G8 0.37 null null 0.16 9c88216e-3efd-47ba-8810-ec1f9177ee4c FN0156 LN56 HR Senior Engineer G4 0.23 null null 0.16 543adc79-164b-474d-aa72-2ac587173849 FN1933 LN33 Operations Senior Engineer G9 0.75 null null 0.16 9fcd0c07-0c42-4f3a-805b-4656d9030fd4 FN1107 LN07 HR Director G5 0.06 null null 0.16 284c253b-d32e-410b-af93-1e1cc9169cd5 FN1059 LN59 Customer Success Director G6 0.74 null null 0.16 19ccc993-4a1a-4995-929e-f02c64daf0ce FN1179 LN79 Sales Engineer II G5 0.84 null null 0.16 2febfa4c-ce4a-49e9-8e1e-9fbdd8a57447 FN1165 LN65 Customer Success VP G8 0.02 null null 0.16 0ee35552-26f0-4f7d-a234-aaf081efc870 FN0072 LN72 HR Director G8 0.84 null null 0.16 0b61941c-930f-4083-b2e1-b4f2cbdf1ca1 FN0224 LN24 HR Engineer I G5 0.6 null null 0.16 5df07f0f-8f55-4096-a0d3-5f7b6ad19cde FN0199 LN99 Finance Analyst G7 0.13 null null 0.16 6c4453eb-f3c8-40bb-a97e-2f60adfa62c4 FN0185 LN85 Finance Director G7 0.03 null null 0.16 7664f626-ef9c-46a3-90da-28101539611b FN1702 LN02 Customer Success Senior Engineer G5 0.06 null null 0.16 b6e1ef6c-6960-47ed-8678-865bbe2d5696 FN1915 LN15 Sales Senior Manager G8 0.92 null null 0.16 6ba93ca9-2bc1-4817-95fd-75ee5fcd4c51 FN0044 LN44 Sales Senior Analyst G7 0.64 null null 0.16 874183b2-3be7-405e-9775-fd58c1fc654b FN1969 LN69 Finance Analyst G7 0.19 null null 0.16 d4c58db1-f7fb-46c3-9299-30d3f8d07256 FN1943 LN43 Sales Engineer II G9 0.32 null null 0.16 8c57dfd5-f076-43a7-8618-9a2f57993552 FN1965 LN65 Finance Senior Analyst G9 0.59 null null 0.16 59e9c7ae-9de5-4ade-a541-96165ce8e088 FN1647 LN47 Sales Senior Engineer G6 0.36 null null 0.16 7365d31b-4c77-4e08-9739-f2b9a3553bcb FN1765 LN65 Customer Success Senior Manager G6 0.17 null null 0.16 32084f0c-1bf4-4438-9923-b784c0d8bcf2 FN1993 LN93 Engineering Senior Analyst G5 0.49 null null 0.16 a1af802d-5121-4ac7-a48a-976ad77dba18 FN1771 LN71 Finance Lead Analyst G7 0.57 null null 0.16 466c0afc-8dc1-4761-b6a6-5793e45b44dc FN1162 LN62 HR Manager G4 0.67 null null 0.16 e58eaff6-37da-436c-98f7-58069e2bbe62 FN1932 LN32 Engineering Engineer II G7 0.16 null null 0.16 4b822bb4-8f37-4151-a03d-b368d56a0a7d FN1218 LN18 Customer Success Senior Analyst G5 0.77 null null 0.16 89d5fa00-6d5a-4c9e-b78b-a3b8ab545006 FN1936 LN36 Engineering Senior Engineer G6 0.5 null null 0.16 e61676b3-b9bd-4cb3-81c0-07b3734e8c53 FN1184 LN84 Operations Manager G4 0.53 null null 0.16 dc5c9737-15e9-4933-9ca5-c05106483ab1 FN1977 LN77 HR Manager G8 0.84 null null 0.16 11f4034b-a7d0-469d-b1b6-e8e7f89edbe3 FN1167 LN67 Finance Manager G6 0.89 null null 0.16 160c3d38-60dd-4e8e-9743-bf2048007d13 FN1994 LN94 HR Engineer II G4 0.66 null null 0.16 bb12b865-bf3c-4334-9c94-986b9bb5482b FN0111 LN11 HR Lead Analyst G8 0.32 null null 0.16 f95664df-ed56-4fdd-8ef7-2

In [0]:
%sql
SELECT manager_id, manager_attrition_rate_pct, manager_attritions_count FROM akash_s_demo.talent.dim_employees GROUP BY manager_id, manager_attrition_rate_pct, manager_attritions_count ORDER BY manager_attrition_rate_pct DESC LIMIT 50;

---------------------------------------------------------------------------
AnalysisException                         Traceback (most recent call last)
File <command-6333049141990838>, line 1
----> 1 get_ipython().run_cell_magic('sql', '', 'SELECT manager_id, manager_attrition_rate_pct, manager_attritions_count FROM akash_s_demo.talent.dim_employees GROUP BY manager_id, manager_attrition_rate_pct, manager_attritions_count ORDER BY manager_attrition_rate_pct DESC LIMIT 50;\n')

File /databricks/python/lib/python3.12/site-packages/IPython/core/interactiveshell.py:2541, in InteractiveShell.run_cell_magic(self, magic_name, line, cell)
   2539 with self.builtin_trap:
   2540     args = (magic_arg_s, cell)
-> 2541     result = fn(*args, **kwargs)
   2543 # The code below prevents the output from being displayed
   2544 # when using magics with decorator @output_can_be_silenced
   2545 # when the last Python token in the expression is a ';'.
   2546 if getattr(fn, magic.MAGIC_OUTPUT_CAN_BE_SI

# 🎯 DATA ENHANCEMENTS TO ENSURE MEANINGFUL QUERY RESULTS

The generated data may not always produce meaningful results for specific queries.
These cells enhance the existing data to guarantee good answers for the 5 key questions.

**Approach:** Modify the DataFrames BEFORE writing to Delta tables to ensure:
1. Each BU has sufficient attrition events (not 0%)
2. Attrition reasons are logic-based and varied
3. Promotions are meaningful per BU
4. Salary comparisons show clear gaps
5. Work-life balance data drives attrition


In [ ]:
# CRITICAL FIX: Modify attrition_snap_df to GUARANTEE meaningful attrition per BU
# Problem: Random attrition may result in 0% for some BUs
# Solution: Ensure each BU has target attrition rate with logic-based reasons

print("=" * 80)
print("🔧 FIXING ATTRITION DATA - Ensuring Meaningful Numbers per BU")
print("=" * 80)

# Target attrition rates by BU (these will be enforced)
bu_target_attrition = {
    "Sales": 0.28,              # 28%
    "Customer Success": 0.22,    # 22%
    "Operations": 0.18,          # 18%
    "Engineering": 0.15,         # 15%
    "Finance": 0.12,            # 12%
    "HR": 0.10                  # 10%
}

# Get employee counts per BU
emp_counts_by_bu = emp_df.groupBy("business_unit").agg(
    count("*").alias("emp_count")
).collect()

bu_emp_count = {row.business_unit: row.emp_count for row in emp_counts_by_bu}

print(f"\\nEmployees per BU:")
for bu, cnt in bu_emp_count.items():
    target_attr = int(cnt * bu_target_attrition.get(bu, 0.15))
    print(f"  {bu}: {cnt} employees → Target {target_attr} attritions ({int(bu_target_attrition.get(bu, 0.15)*100)}%)")

# For EACH BU, ensure we have target number of attritions
# We'll mark specific employees for attrition based on BU target rates

from pyspark.sql.window import Window

# Create a deterministic attrition assignment per BU
emp_with_bu_rank = emp_df.select("employee_id", "business_unit", "tenure_years").withColumn(
    "bu_rank",
    row_number().over(Window.partitionBy("business_unit").orderBy(rand(seed=SEED+100)))
)

# Add BU target attrition rate
bu_target_map_args = []
for bu, rate in bu_target_attrition.items():
    bu_target_map_args.append(lit(bu))
    bu_target_map_args.append(lit(rate))

bu_target_map_sql = create_map(*bu_target_map_args)

emp_with_bu_rank = emp_with_bu_rank.withColumn(
    "bu_target_rate",
    bu_target_map_sql[col("business_unit")]
).withColumn(
    # Get total employees in this BU
    "bu_total",
    count("*").over(Window.partitionBy("business_unit"))
).withColumn(
    # Target attrition count for this BU
    "bu_target_count",
    (col("bu_total") * col("bu_target_rate")).cast("int")
).withColumn(
    # Mark this employee for attrition if their rank is within target count
    "should_attrit",
    when(col("bu_rank") <= col("bu_target_count"), lit(1)).otherwise(lit(0))
)

# Get list of employees marked for attrition
employees_to_attrit = emp_with_bu_rank.filter(col("should_attrit") == 1).select("employee_id", "business_unit")

print(f"\\n✅ Marked employees for attrition per BU:")
employees_to_attrit.groupBy("business_unit").count().orderBy("business_unit").show()

# Now update attrition_snap_df: for marked employees, set attrition_flag=1 in a random recent month
# Join with snapshot data and update attrition_flag

attrition_snap_with_marker = attrition_snap_df.join(
    employees_to_attrit.withColumn("marked_for_attr", lit(1)),
    "employee_id",
    "left"
).na.fill({"marked_for_attr": 0})

# For marked employees, pick ONE random recent snapshot (last 12 months) and set attrition
recent_date = today - datetime.timedelta(days=365)
recent_date_str = recent_date.isoformat()

attrition_snap_enhanced = attrition_snap_with_marker.withColumn(
    # Random assignment: for marked employees, set attrition in one random recent snapshot
    "should_set_attr",
    when(
        (col("marked_for_attr") == 1) & 
        (col("snapshot_date") >= lit(recent_date_str)) &
        (rand(seed=SEED+101) < lit(1.0 / 12)),  # 1/12 chance per snapshot in last year
        lit(1)
    ).otherwise(lit(0))
).withColumn(
    # Update attrition_flag: keep existing OR set new
    "attrition_flag",
    when(col("should_set_attr") == 1, lit(1)).otherwise(col("attrition_flag"))
).drop("marked_for_attr", "should_set_attr")

# Update attrition_snap_df
attrition_snap_df = attrition_snap_enhanced

print(f"\\n✅ Enhanced attrition data")
print(f"\\n📊 Attrition events by BU:")

# Check which attrition column exists (handles both fresh run and re-run scenarios)
attrition_cols = attrition_snap_df.columns
if "attrition_flag" in attrition_cols:
    attr_col = "attrition_flag"
elif "latest_attrition_flag" in attrition_cols:
    attr_col = "latest_attrition_flag"
else:
    print("⚠️ No attrition flag column found")
    attr_col = None

if attr_col:
    # Join with emp_df to get business_unit if not already present
    if "business_unit" not in attrition_cols:
        attrition_with_bu_check = attrition_snap_df.join(
            emp_df.select("employee_id", "business_unit"),
            "employee_id",
            "left"
        )
    else:
        attrition_with_bu_check = attrition_snap_df
    
    attrition_with_bu_check.filter(col(attr_col) == 1).groupBy("business_unit").count().orderBy(desc("count")).show()


In [ ]:
# Enhancement 2: Logic-Based Attrition Reasons
# Replace random reasons with meaningful, correlated reasons

print("=" * 80)
print("🔧 ENHANCEMENT 2: Logic-Based Attrition Reasons")
print("=" * 80)

# Get latest compensation data for attrition logic
latest_comp = comp_df.filter(col("year") == latest_year).select(
    "employee_id",
    col("compa_ratio").alias("latest_compa"),
    col("salary_growth_pct").alias("latest_growth")
)

# Get mobility data
mobility_for_attr = role_history_df.groupBy("employee_id").agg(
    sum("promotion_flag").alias("promotion_count"),
    count("*").alias("role_count")
)

# Join attrition with comp and mobility data
attrition_with_context = attrition_snap_df.join(
    emp_df.select("employee_id", "business_unit", "tenure_years"),
    "employee_id",
    "left"
).join(
    latest_comp,
    "employee_id",
    "left"
).join(
    mobility_for_attr,
    "employee_id",
    "left"
).na.fill({"promotion_count": 0, "role_count": 1, "latest_compa": 1.0, "latest_growth": 0.0})

# Determine which attrition flag column to use
attr_flag_col = "attrition_flag" if "attrition_flag" in attrition_with_context.columns else "latest_attrition_flag"

# Update attrition_reason with LOGIC-BASED assignment
attrition_with_logic = attrition_with_context.withColumn(
    "attrition_reason_new",
    when(
        col(attr_flag_col) == 0,
        lit(None)  # No attrition
    ).when(
        # Low Pay: compa_ratio < 0.9 AND low salary growth
        (col("latest_compa") < 0.9) & (col("latest_growth") < 3.0),
        lit("Low Pay")
    ).when(
        # Career Stagnation: no promotions AND tenure > 3 years
        (col("promotion_count") == 0) & (col("tenure_years") > 3),
        lit("Career Stagnation")
    ).when(
        # Manager Issues: 25% of remaining
        rand(seed=SEED+110) < 0.35,
        lit("Manager Issues")
    ).when(
        # Work-Life Balance: assign based on BU (Sales/CS have more WLB issues)
        col("business_unit").isin(["Sales", "Customer Success"]) & (rand(seed=SEED+111) < 0.20),
        lit("Work-Life Balance")
    ).when(
        # Personal: smaller portion
        rand(seed=SEED+112) < 0.50,
        lit("Personal")
    ).otherwise(
        lit("Relocation")
    )
).drop("attrition_reason").withColumnRenamed("attrition_reason_new", "attrition_reason")

# Update the main DF
attrition_snap_df = attrition_with_logic

print(f"\\n✅ Applied logic-based attrition reasons")
print(f"\\n📊 Attrition Reasons Distribution:")
# Use the appropriate attrition flag column
attr_display_col = "attrition_flag" if "attrition_flag" in attrition_snap_df.columns else "latest_attrition_flag"
attrition_snap_df.filter(col(attr_display_col) == 1).groupBy("attrition_reason").agg(
    count("*").alias("count")
).withColumn(
    "percentage",
    round(col("count") * 100.0 / sum("count").over(Window.partitionBy()), 1)
).orderBy(desc("count")).show()


In [ ]:
# Enhancement 3: Increase Promotions to Meaningful Numbers
# Ensure ~12-15% annual promotion rate with BU differentiation

print("=" * 80)
print("🔧 ENHANCEMENT 3: Increasing Promotion Numbers")
print("=" * 80)

# BU-specific promotion multipliers to reach target numbers
bu_promotion_mult = {
    "Engineering": 1.8,      # Highest promotions
    "Sales": 1.5,
    "Operations": 1.2,
    "Customer Success": 1.0,
    "Finance": 0.9,
    "HR": 0.7              # Smaller team
}

bu_promo_map_args = []
for bu, mult in bu_promotion_mult.items():
    bu_promo_map_args.append(lit(bu))
    bu_promo_map_args.append(lit(mult))

bu_promo_map_sql = create_map(*bu_promo_map_args)

# Add BU info to role_history
role_with_bu = role_history_df.join(
    emp_df.select("employee_id", "business_unit"),
    "employee_id",
    "left"
).withColumn(
    "bu_promo_mult",
    bu_promo_map_sql[col("business_unit")]
)

# Enhance promotion_flag: keep existing + add more based on grade progression
role_enhanced = role_with_bu.withColumn(
    "promotion_flag_new",
    when(
        col("promotion_flag") == 1,  # Keep existing
        lit(1)
    ).when(
        # Add more promotions: if grade increased AND random based on BU mult
        (col("prev_grade_rank").isNotNull()) &
        (col("grade_rank") > col("prev_grade_rank")) &
        (rand(seed=SEED+120) < (lit(0.15) * col("bu_promo_mult"))),
        lit(1)
    ).otherwise(lit(0))
).drop("promotion_flag").withColumnRenamed("promotion_flag_new", "promotion_flag")

# Update role_history_df
role_history_df = role_enhanced

print(f"\\n✅ Enhanced promotion data")
print(f"\\n📊 Promotions by BU:")
role_history_df.filter(col("promotion_flag") == 1).groupBy("business_unit").agg(
    countDistinct("employee_id").alias("employees_promoted"),
    count("*").alias("total_promotions")
).orderBy(desc("total_promotions")).show()

print(f"\\n📊 Overall promotion stats:")
total_promotions = role_history_df.filter(col("promotion_flag") == 1).count()
total_role_changes = role_history_df.count()
print(f"  Total promotions: {total_promotions}")
print(f"  Total role changes: {total_role_changes}")
print(f"  Promotion rate: {round(total_promotions / total_role_changes * 100, 1)}%")


In [ ]:
# Enhancement 4: Industry Salary Comparison
# Add industry benchmark data to compensation table

print("=" * 80)
print("🔧 ENHANCEMENT 4: Industry Salary Comparison")
print("=" * 80)

# Industry median salaries by grade (India base)
industry_median_by_grade = {
    "G4": 450000,   # 10% above internal
    "G5": 750000,   # 7% above internal
    "G6": 1150000,  # 4% above internal
    "G7": 1700000,  # On par
    "G8": 2600000,  # 4% above internal
    "G9": 4200000   # 5% above internal
}

# Build map for industry median
industry_map_args = []
for g, v in industry_median_by_grade.items():
    industry_map_args.append(lit(g))
    industry_map_args.append(lit(v))

industry_median_map_sql = create_map(*industry_map_args)

# Add industry comparison columns to compensation DF
comp_enhanced = comp_df.withColumn(
    "industry_median_salary",
    (industry_median_map_sql[col("grade")] * col("region_mult")).cast("long")
).withColumn(
    "salary_gap_pct",
    round((col("salary") - col("industry_median_salary")) / col("industry_median_salary") * 100, 1)
).withColumn(
    "below_market_flag",
    when(col("salary_gap_pct") < -10, lit(1)).otherwise(lit(0))
)

# Update comp_df
comp_df = comp_enhanced

print(f"\n✅ Added industry salary comparison")
print(f"\n📊 Salary vs Industry by Grade:")
comp_df.filter(col("year") == latest_year).groupBy("grade").agg(
    round(avg("salary")).alias("our_avg_salary"),
    round(avg("industry_median_salary")).alias("industry_median"),
    round(avg("salary_gap_pct"), 1).alias("avg_gap_pct"),
    round(sum("below_market_flag") * 100.0 / count("*"), 1).alias("pct_below_market")
).orderBy("grade").show()

print(f"\n📊 Below Market Analysis:")
below_market_stats = comp_df.filter(col("year") == latest_year).agg(
    round(sum("below_market_flag") * 100.0 / count("*"), 1).alias("pct_below_market"),
    count(when(col("below_market_flag") == 1, 1)).alias("count_below_market")
).collect()[0]
print(f"  % of employees paid below market: {below_market_stats['pct_below_market']}%")
print(f"  Total employees below market: {below_market_stats['count_below_market']}")


In [ ]:
# Enhancement 5: Work-Life Balance Metrics
# Add WLB metrics to attrition snapshots

print("=" * 80)
print("🔧 ENHANCEMENT 5: Work-Life Balance Metrics")
print("=" * 80)

# BU-specific baseline work hours
bu_base_hours = {
    "Sales": 52,
    "Customer Success": 48,
    "Operations": 45,
    "Engineering": 42,
    "Finance": 42,
    "HR": 40
}

bu_hours_map_args = []
for bu, hrs in bu_base_hours.items():
    bu_hours_map_args.append(lit(bu))
    bu_hours_map_args.append(lit(hrs))

bu_hours_map_sql = create_map(*bu_hours_map_args)

# Add BU info to attrition snapshots for WLB calculation
attrition_with_bu = attrition_snap_df.join(
    emp_df.select("employee_id", "business_unit", "current_grade"),
    "employee_id",
    "left"
)

# Calculate work-life balance metrics
wlb_enhanced = attrition_with_bu.withColumn(
    "base_hours",
    bu_hours_map_sql[col("business_unit")]
).withColumn(
    # Add variation: higher grades work more, plus random variation
    "grade_hours_add",
    when(col("current_grade") == "G9", lit(8))
    .when(col("current_grade") == "G8", lit(6))
    .when(col("current_grade") == "G7", lit(4))
    .when(col("current_grade") == "G6", lit(2))
    .otherwise(lit(0))
).withColumn(
    "work_hours_per_week",
    round(
        col("base_hours") + 
        col("grade_hours_add") + 
        (rand(seed=SEED+130) * 10 - 3),  # Random variation -3 to +7
        1
    )
).withColumn(
    "overtime_hours_per_month",
    when(
        col("work_hours_per_week") > 40,
        ((col("work_hours_per_week") - 40) * 4).cast("int")
    ).otherwise(lit(0))
).withColumn(
    # Stress level correlated with work hours
    "stress_level",
    round(
        when(col("work_hours_per_week") > 55, lit(8.0) + rand(seed=SEED+131) * 2)
        .when(col("work_hours_per_week") > 50, lit(6.0) + rand(seed=SEED+132) * 2)
        .when(col("work_hours_per_week") > 45, lit(4.0) + rand(seed=SEED+133) * 2)
        .otherwise(lit(2.0) + rand(seed=SEED+134) * 2),
        1
    )
).withColumn(
    "burnout_flag",
    when((col("work_hours_per_week") > 55) & (col("stress_level") > 7), lit(1))
    .otherwise(lit(0))
).withColumn(
    "wlb_score",
    round(lit(10) - col("stress_level") * 0.8, 1)
)

# Update attrition_snap_df with WLB metrics
attrition_snap_df = wlb_enhanced

print(f"\n✅ Added work-life balance metrics")
print(f"\n📊 Work Hours by BU (Latest Snapshot):")
latest_snapshot = attrition_snap_df.agg(max("snapshot_date")).collect()[0][0]
attrition_snap_df.filter(col("snapshot_date") == lit(latest_snapshot)).groupBy("business_unit").agg(
    round(avg("work_hours_per_week"), 1).alias("avg_hours_per_week"),
    round(avg("stress_level"), 1).alias("avg_stress"),
    round(avg("wlb_score"), 1).alias("avg_wlb_score"),
    round(sum("burnout_flag") * 100.0 / count("*"), 1).alias("pct_burnout")
).orderBy(desc("avg_hours_per_week")).show()

print(f"\n📊 WLB Impact on Attrition:")
wlb_categories = attrition_snap_df.filter(col("snapshot_date") == lit(latest_snapshot)).withColumn(
    "wlb_category",
    when(col("work_hours_per_week") > 55, lit("Burnout (>55 hrs)"))
    .when(col("work_hours_per_week") > 50, lit("Poor (50-55 hrs)"))
    .when(col("work_hours_per_week") > 45, lit("Average (45-50 hrs)"))
    .otherwise(lit("Good (≤45 hrs)"))
).groupBy("wlb_category").agg(
    count("*").alias("employee_count"),
    sum("attrition_flag").alias("attritions"),
    round(sum("attrition_flag") * 100.0 / count("*"), 1).alias("attrition_rate_pct")
).orderBy(desc("attrition_rate_pct"))

wlb_categories.show()


In [ ]:
# Enhancement 6: Update Attrition Reasons with WLB and Salary Data
# Refine attrition reasons to incorporate new metrics

print("=" * 80)
print("🔧 ENHANCEMENT 6: Refining Attrition Reasons with WLB & Salary Data")
print("=" * 80)

# Get latest comp data for below-market flag
latest_comp_enhanced = comp_df.filter(col("year") == latest_year).select(
    "employee_id",
    col("compa_ratio").alias("latest_compa"),
    col("salary_gap_pct").alias("latest_salary_gap"),
    col("below_market_flag").alias("is_below_market")
)

# Join attrition with enhanced comp data
attrition_final = attrition_snap_df.join(
    latest_comp_enhanced,
    "employee_id",
    "left"
).join(
    mobility_for_attr,
    "employee_id",
    "left"
).na.fill({
    "promotion_count": 0,
    "is_below_market": 0,
    "latest_compa": 1.0,
    "latest_salary_gap": 0.0
})

# Determine which attrition flag column to use
attr_col_21 = "attrition_flag" if "attrition_flag" in attrition_final.columns else "latest_attrition_flag"

# Update attrition reasons with ENHANCED logic incorporating WLB and salary gaps
attrition_final = attrition_final.withColumn(
    "attrition_reason_final",
    when(
        col(attr_col_21) == 0,
        lit(None)
    ).when(
        # Priority 1: Below Market Pay (compa < 0.9 OR below_market_flag)
        (col("is_below_market") == 1) | ((col("latest_compa") < 0.9) & (col("latest_salary_gap") < -5)),
        lit("Low Pay")
    ).when(
        # Priority 2: Work-Life Balance (burnout flag)
        col("burnout_flag") == 1,
        lit("Work-Life Balance")
    ).when(
        # Priority 3: Career Stagnation (no promotions + tenure > 3)
        (col("promotion_count") == 0) & (col("tenure_years") > 3),
        lit("Career Stagnation")
    ).when(
        # Priority 4: Manager Issues (35% of remaining)
        rand(seed=SEED+140) < 0.35,
        lit("Manager Issues")
    ).when(
        # Priority 5: Work-Life Balance for high stress (not burnout but stressed)
        (col("work_hours_per_week") > 50) & (col("stress_level") > 6) & (rand(seed=SEED+141) < 0.40),
        lit("Work-Life Balance")
    ).when(
        # Priority 6: Personal
        rand(seed=SEED+142) < 0.50,
        lit("Personal")
    ).otherwise(
        lit("Relocation")
    )
).drop("attrition_reason").withColumnRenamed("attrition_reason_final", "attrition_reason")

# Update attrition_snap_df
attrition_snap_df = attrition_final

print(f"\n✅ Enhanced attrition reasons with WLB and salary data")
print(f"\n📊 Final Attrition Reasons Distribution:")
reason_dist = attrition_snap_df.filter(col("attrition_flag") == 1).groupBy("attrition_reason").agg(
    count("*").alias("count")
).withColumn(
    "percentage",
    round(col("count") * 100.0 / sum("count").over(Window.partitionBy()), 1)
).orderBy(desc("count"))

reason_dist.show()

print(f"\n📊 Correlation: Below Market Pay → Attrition")
below_market_attr = attrition_snap_df.filter(col("snapshot_date") == lit(latest_snapshot)).groupBy("is_below_market").agg(
    count("*").alias("employee_count"),
    sum("attrition_flag").alias("attritions"),
    round(sum("attrition_flag") * 100.0 / count("*"), 1).alias("attrition_rate_pct")
)
below_market_attr.show()


In [ ]:
# Enhancement 7: Re-compute Enriched Employees with New Metrics

print("=" * 80)
print("🔧 ENHANCEMENT 7: Updating Enriched Employees Table")
print("=" * 80)

# Re-compute employees_enriched_df with ALL new metrics

# Latest snapshot with WLB metrics
latest_snapshot_df = attrition_snap_df.filter(col("snapshot_date") == lit(latest_snapshot)).select(
    "employee_id",
    col("attrition_flag").alias("latest_attrition_flag"),
    "exit_date",
    "attrition_reason",
    "predicted_attrition_risk",
    "career_stagnation_flag",
    "work_hours_per_week",
    "overtime_hours_per_month",
    "stress_level",
    "burnout_flag",
    "wlb_score"
)

# Latest comp with industry comparison
latest_comp_full = comp_df.filter(col("year") == latest_year).select(
    "employee_id",
    col("salary").alias("current_salary"),
    col("bonus").alias("current_bonus"),
    col("compa_ratio").alias("current_compa_ratio"),
    col("salary_growth_pct").alias("latest_salary_growth_pct"),
    "industry_median_salary",
    "salary_gap_pct",
    "below_market_flag"
)

# Latest performance
latest_perf_full = perf_df.filter(col("year") == latest_year).select(
    "employee_id",
    col("rating").alias("latest_rating"),
    col("rating_3yr_avg").alias("latest_rating_3yr_avg"),
    col("potential_flag").alias("high_potential_flag")
)

# Mobility counts
mobility_final = role_history_df.groupBy("employee_id").agg(
    count("*").alias("total_role_changes"),
    sum("promotion_flag").alias("total_promotions"),
    max("role_end_date_clamped").alias("last_role_change_date")
)

# Build comprehensive employees_enriched_df
employees_enriched_df = (
    emp_df
    .join(mobility_final, "employee_id", "left")
    .join(latest_comp_full, "employee_id", "left")
    .join(latest_perf_full, "employee_id", "left")
    .join(latest_snapshot_df, "employee_id", "left")
)

# Fill null values
employees_enriched_df = employees_enriched_df.na.fill({
    "total_role_changes": 1,
    "total_promotions": 0,
    "current_compa_ratio": 1.0,
    "latest_rating": 3,
    "latest_rating_3yr_avg": 3.0,
    "high_potential_flag": 0,
    "latest_attrition_flag": 0,
    "career_stagnation_flag": 0,
    "work_hours_per_week": 42.0,
    "stress_level": 4.0,
    "burnout_flag": 0,
    "wlb_score": 6.0,
    "below_market_flag": 0,
    "salary_gap_pct": 0.0
})

# Add manager aggregates
manager_perf = perf_df.filter(col("year") == latest_year).groupBy("reviewer_id").agg(
    round(avg("rating"), 2).alias("manager_avg_team_rating"),
    count("*").alias("manager_team_size")
)

# Manager attrition stats from latest snapshot
manager_attr = attrition_snap_df.filter(col("snapshot_date") == lit(latest_snapshot)).groupBy("attrition_manager_id").agg(
    sum("attrition_flag").alias("manager_attritions_count"),
    round(sum("attrition_flag") * 100.0 / count("*"), 1).alias("manager_attrition_rate_pct")
)

employees_enriched_df = employees_enriched_df.join(
    manager_perf,
    employees_enriched_df.manager_id == manager_perf.reviewer_id,
    "left"
).drop("reviewer_id")

employees_enriched_df = employees_enriched_df.join(
    manager_attr,
    employees_enriched_df.manager_id == manager_attr.attrition_manager_id,
    "left"
).drop("attrition_manager_id")

# Fill manager nulls
employees_enriched_df = employees_enriched_df.na.fill({
    "manager_avg_team_rating": 3.0,
    "manager_team_size": 0,
    "manager_attritions_count": 0,
    "manager_attrition_rate_pct": 0.0
})

# Compute comprehensive attrition risk score
employees_enriched_df = employees_enriched_df.withColumn(
    "attrition_risk_score",
    round(
        lit(0.03)
        + when(col("tenure_years") < 1, 0.15).otherwise(0.0)
        + when(col("career_stagnation_flag") == 1, 0.12).otherwise(0.0)
        + when(col("total_promotions") == 0, 0.08).otherwise(0.0)
        + when(col("below_market_flag") == 1, 0.18).otherwise(0.0)
        + when(col("burnout_flag") == 1, 0.15).otherwise(0.0)
        + when(col("manager_attrition_rate_pct") > 20, 0.08).otherwise(0.0)
        - when(col("latest_rating_3yr_avg") >= 4.0, 0.08).otherwise(0.0)
        - when(col("high_potential_flag") == 1, 0.06).otherwise(0.0),
        3
    )
)

print(f"\n✅ Updated employees_enriched_df with all metrics")
print(f"\n📊 Sample of enriched data:")
display(employees_enriched_df.select(
    "employee_id", "name", "business_unit", "current_role",
    "tenure_years", "total_promotions", "current_salary",
    "below_market_flag", "work_hours_per_week", "burnout_flag",
    "attrition_risk_score", "latest_attrition_flag"
).limit(10))


In [ ]:
# Final Step: Re-write All Enhanced Delta Tables

print("=" * 80)
print("💾 FINAL STEP: Writing Enhanced Data to Delta Tables")
print("=" * 80)

# Verify counts before writing
print("\n📊 Final Data Counts:")
print(f"  dim_employees: {employees_enriched_df.count()}")
print(f"  fact_role_history: {role_history_df.count()}")
print(f"  fact_performance: {perf_df.count()}")
print(f"  fact_compensation: {comp_df.count()}")
print(f"  fact_attrition_snapshots: {attrition_snap_df.count()}")

# Write enhanced tables
database = "akash_s_demo.talent"

print(f"\n💾 Writing to database: {database}")
print("  → dim_employees...")
employees_enriched_df.write.format("delta").mode("overwrite").saveAsTable(f"{database}.dim_employees")

print("  → fact_role_history...")
role_history_df.write.format("delta").mode("overwrite").saveAsTable(f"{database}.fact_role_history")

print("  → fact_performance...")
perf_df.write.format("delta").mode("overwrite").saveAsTable(f"{database}.fact_performance")

print("  → fact_compensation...")
comp_df.write.format("delta").mode("overwrite").saveAsTable(f"{database}.fact_compensation")

print("  → fact_attrition_snapshots...")
attrition_snap_df.write.format("delta").mode("overwrite").saveAsTable(f"{database}.fact_attrition_snapshots")

print("\n" + "=" * 80)
print("✅ ALL ENHANCEMENTS COMPLETE!")
print("=" * 80)
print("\nEnhanced Features:")
print("  ✅ 1. BU-specific attrition rates (10%-28%)")
print("  ✅ 2. Logic-based attrition reasons (Low Pay, WLB, Career Stagnation, etc.)")
print("  ✅ 3. Increased meaningful promotions (12-15% annual rate)")
print("  ✅ 4. Industry salary comparison (median, gap%, below_market_flag)")
print("  ✅ 5. Work-life balance metrics (hours, stress, burnout)")
print("  ✅ 6. Enhanced attrition risk scoring")
print("  ✅ 7. Manager performance and attrition aggregates")
print("\n🎯 Your 5 questions will now have MEANINGFUL answers!")
print("=" * 80)


# 🎯 Data Enhancement Summary

## All 5 Enhancements Completed!

### Enhancement 1: BU-Specific Attrition Rates
- **Sales**: 28% (highest pressure)
- **Customer Success**: 22%
- **Operations**: 18%
- **Engineering**: 15%
- **Finance**: 12%
- **HR**: 10% (best retention)

### Enhancement 2: Logic-Based Attrition Reasons
Replaced random reasons with meaningful correlations:
- **Low Pay**: 30-35% (linked to below_market_flag, low compa_ratio)
- **Work-Life Balance**: 15-20% (linked to burnout_flag, high hours)
- **Career Stagnation**: 15-20% (linked to no promotions + tenure > 3 years)
- **Manager Issues**: 20-25%
- **Personal**: 5-10%
- **Relocation**: 3-5%

### Enhancement 3: Increased Promotions
- **Annual promotion rate**: 12-15%
- **Total promotions/year**: ~250-350 across all BUs
- **BU-specific rates**: Engineering highest, HR lowest

### Enhancement 4: Industry Salary Comparison
New columns in `fact_compensation`:
- `industry_median_salary`: Benchmark by grade + region
- `salary_gap_pct`: Your salary vs industry (%)
- `below_market_flag`: If gap < -10%

**Key Finding**: 30-40% of employees are paid below market → 2-3x higher attrition

### Enhancement 5: Work-Life Balance Metrics
New columns in `fact_attrition_snapshots`:
- `work_hours_per_week`: 40-70 range
- `overtime_hours_per_month`: 0-60
- `stress_level`: 1-10 scale
- `burnout_flag`: hours > 55/week AND stress > 7
- `wlb_score`: 1-10

**Key Finding**: 20% work >55 hrs/week, 12% have burnout → 3x higher attrition

---

## 📊 Now Your Questions Have Meaningful Answers!

### Q1: What are major reasons for attrition?
Run this query to see the distribution:
```sql
SELECT attrition_reason, COUNT(*) as count, 
       ROUND(COUNT(*) * 100.0 / SUM(COUNT(*)) OVER(), 1) as percentage
FROM akash_s_demo.talent.fact_attrition_snapshots
WHERE attrition_flag = 1
GROUP BY attrition_reason
ORDER BY count DESC;
```

### Q2: Which BU has highest attrition?
```sql
SELECT business_unit,
       SUM(attrition_flag) as attritions,
       COUNT(DISTINCT employee_id) as employees,
       ROUND(SUM(attrition_flag) * 100.0 / COUNT(DISTINCT employee_id), 1) as attrition_rate_pct
FROM akash_s_demo.talent.fact_attrition_snapshots
GROUP BY business_unit
ORDER BY attrition_rate_pct DESC;
```

### Q3: Average promotions per BU?
```sql
SELECT business_unit,
       COUNT(DISTINCT CASE WHEN promotion_flag = 1 THEN employee_id END) as employees_promoted,
       SUM(promotion_flag) as total_promotions
FROM akash_s_demo.talent.fact_role_history
GROUP BY business_unit
ORDER BY total_promotions DESC;
```

### Q4: Are salaries on par with industry?
```sql
SELECT grade,
       ROUND(AVG(salary)) as our_avg_salary,
       ROUND(AVG(industry_median_salary)) as industry_avg,
       ROUND(AVG(salary_gap_pct), 1) as avg_gap_pct,
       ROUND(SUM(below_market_flag) * 100.0 / COUNT(*), 1) as pct_below_market
FROM akash_s_demo.talent.fact_compensation
WHERE year = 2025
GROUP BY grade
ORDER BY grade;
```

### Q5: Work-life balance issues leading to attrition?
```sql
SELECT 
  CASE 
    WHEN work_hours_per_week > 55 THEN 'Burnout (>55 hrs)'
    WHEN work_hours_per_week > 50 THEN 'Poor (50-55 hrs)'
    WHEN work_hours_per_week > 45 THEN 'Average (45-50 hrs)'
    ELSE 'Good (≤45 hrs)'
  END as wlb_category,
  business_unit,
  COUNT(*) as employee_count,
  SUM(attrition_flag) as attritions,
  ROUND(SUM(attrition_flag) * 100.0 / COUNT(*), 1) as attrition_rate_pct
FROM akash_s_demo.talent.fact_attrition_snapshots
WHERE snapshot_date = (SELECT MAX(snapshot_date) FROM akash_s_demo.talent.fact_attrition_snapshots)
GROUP BY wlb_category, business_unit
ORDER BY attrition_rate_pct DESC;
```

---

## ✅ Next Steps
1. Run the cells from top to bottom to generate the enhanced data
2. Test the SQL queries above to verify meaningful results
3. Use the enriched data in your LangGraph agent for intelligent Q&A
